In [1]:
import numpy as np
import pandas as pd
from collections import namedtuple

from pathlib import Path

In [2]:
N_SAMPLES = 1000
SEED = 42
RNG = np.random.default_rng(seed=SEED)
COLS_DUMMY_DATA = ['type', 'problem', 'action']
TOTAL_POSSIBILITY_FAILURES = 0.4
TYPE_MAPPING = {
    'Reguläre Wartung': 'Wartung',
    'Unerwarteter Fehler': 'Störungsmeldung',
}
OBJ_IDS_2_TXT = {
    1: 'Fräsmaschine-FS435X',
    2: 'Schleifmaschine-S4x87',
    3: 'Bohrbearbeitungszentrum-BBZ35',
}
STARTING_DATE = pd.to_datetime('2022-01-01')
ENDING_DATE = pd.to_datetime('2024-08-07')
DATASET_FEATURES = [
    'VorgangsID',
    'ObjektID',
    'HObjektText',
    'VorgangsTypName',
    'VorgangsBeschreibung',
    'ErledigungsBeschreibung',
    'ErstellungsDatum',
    'VorgangsDatum',
    'Arbeitsbeginn',
    'ErledigungsDatum',
]
DF_SKELLETON = {feat: [] for feat in DATASET_FEATURES}

In [3]:
source = '../data/Dummy_Data.xlsx'
dest = f'../data/Dummy_Dataset_N_{N_SAMPLES}.csv'
pth_source = Path(source)
pth_dest = Path(dest)
assert pth_source.exists()

In [4]:
def read_dummy_data(pth_data, columns=COLS_DUMMY_DATA):
    data = pd.read_excel(pth_data)
    data.columns = columns.copy()
    
    return data

In [5]:
data = read_dummy_data(pth_source)
data.head()

type                    problem  \
0     Reguläre Wartung       Schmierung der Lager   
1  Unerwarteter Fehler           Motorüberhitzung   
2     Reguläre Wartung  Überprüfung der Hydraulik   
3  Unerwarteter Fehler           Elektronikfehler   
4     Reguläre Wartung  Kalibrierung der Sensoren   

                                              action  
0                      Nachfüllen des Schmiermittels  
1                         Austausch des Kühlgebläses  
2  Reinigung und Nachfüllen der Hydraulikflüssigkeit  
3                     Austausch der defekten Platine  
4                   Justierung und Test der Sensoren

In [6]:
def make_subset(data, target_type, type_mapping=TYPE_MAPPING):
    Entry = namedtuple('ProblemActionPairs', ['type', 'problem', 'action'])
    entries = []
    data_subset = data.loc[data['type']==target_type,:].copy()

    for row in data_subset.itertuples(index=False):
        type_mapped = type_mapping[row.type]
        entries.append(Entry(type_mapped, row.problem, row.action))

    return entries

## Activity Types

- relevant activity types:
    - 'Reparaturauftrag (Portal)'
    - 'Störungsmeldung'
    - 'Wartung'
- ``regular`` --> 'Wartung'
- ``failures`` --> 'Störungsmeldung'

### Failures

In [7]:
failures = make_subset(data, target_type='Unerwarteter Fehler')
failures[:10]

[ProblemActionPairs(type='Störungsmeldung', problem='Motorüberhitzung', action='Austausch des Kühlgebläses'),
 ProblemActionPairs(type='Störungsmeldung', problem='Elektronikfehler', action='Austausch der defekten Platine'),
 ProblemActionPairs(type='Störungsmeldung', problem='Getriebeausfall', action='Reparatur und Austausch der beschädigten Zahnräder'),
 ProblemActionPairs(type='Störungsmeldung', problem='Leckage in der Hydraulikleitung', action='Abdichtung der Leckstelle und Nachfüllen der Hydraulikflüssigkeit'),
 ProblemActionPairs(type='Störungsmeldung', problem='Ausfall der Steuerungseinheit', action='Neustart und Software-Update der Steuerungseinheit'),
 ProblemActionPairs(type='Störungsmeldung', problem='Bruch eines Zahnriemens', action='Austausch des Zahnriemens'),
 ProblemActionPairs(type='Störungsmeldung', problem='Kurzschluss im Schaltschrank', action='Austausch der Sicherungen und Kabel'),
 ProblemActionPairs(type='Störungsmeldung', problem='Vibrationsprobleme am Motor', ac

### Regular Maintenance

In [8]:
regular = make_subset(data, target_type='Reguläre Wartung')
regular[:10]

[ProblemActionPairs(type='Wartung', problem='Schmierung der Lager', action='Nachfüllen des Schmiermittels'),
 ProblemActionPairs(type='Wartung', problem='Überprüfung der Hydraulik', action='Reinigung und Nachfüllen der Hydraulikflüssigkeit'),
 ProblemActionPairs(type='Wartung', problem='Kalibrierung der Sensoren', action='Justierung und Test der Sensoren'),
 ProblemActionPairs(type='Wartung', problem='Reinigung der Luftfilter', action='Austausch der Luftfilter'),
 ProblemActionPairs(type='Wartung', problem='Überprüfung der Sicherheitsvorrichtungen', action='Funktionstest und Justierung der Sicherheitsvorrichtungen'),
 ProblemActionPairs(type='Wartung', problem='Inspektion der Förderbänder', action='Einstellung und Austausch abgenutzter Teile'),
 ProblemActionPairs(type='Wartung', problem='Überprüfung der Druckventile', action='Reinigung und Einstellung der Druckventile'),
 ProblemActionPairs(type='Wartung', problem='Test der Not-Aus-Schalter', action='Test und Austausch defekter Not-Au

## ObjectIDs and HObjektTexts

In [9]:
def random_objects(mapping, rng, n_samples):
    max_val = max(mapping.keys())
    rands = rng.integers(1, max_val+1, size=n_samples)

    obj_ids = rands.tolist()
    texts =[mapping[obj_id] for obj_id in obj_ids]

    return obj_ids, texts

## Random Dates

In [10]:
def random_dates(start, end, rng, n_samples):

    start_u = start.value//10**9
    end_u = end.value//10**9
    days_to_finish = rng.exponential(1.3, n_samples).astype(np.int_)
    td = pd.to_timedelta(days_to_finish, unit='day')

    creation_dates = pd.to_datetime(rng.integers(start_u, end_u, n_samples), unit='s').normalize()
    done_dates = creation_dates + td

    return creation_dates.to_list(), done_dates.to_list()

## Random descriptions

proportions:
- regular: 0.6
- failure: 0.4

In [11]:
def random_descriptions(failures, regular, target_prop_fail, rng, n_samples):
    poss_per_entry_fail = target_prop_fail / len(failures)
    poss_per_entry_regular = (1 - target_prop_fail) / len(regular)

    failure_possibilities = np.full(len(failures), poss_per_entry_fail)
    regular_possibilities = np.full(len(regular), poss_per_entry_regular)
    possibilities = np.concatenate((failure_possibilities, regular_possibilities))

    content_descriptions = failures.copy()
    content_descriptions.extend(regular.copy())

    return rng.choice(content_descriptions, size=n_samples, p=possibilities)

def description_parts(descriptions):
    types = descriptions[:,0].tolist()
    todo = descriptions[:,1].tolist()
    dones = descriptions[:,2].tolist()

    return types, todo, dones

# Complete Dataset

In [12]:
def create_dataset(df_skelleton, type_failure, type_regular, starting_date, ending_date, rng, n_samples):
    df_dict = df_skelleton.copy()
    
    failures = make_subset(data, target_type=type_failure)
    regular = make_subset(data, target_type=type_regular)
    
    event_ids = list(range(1,n_samples+1))
    obj_ids, txts = random_objects(OBJ_IDS_2_TXT, rng, n_samples)
    creation_dates, done_dates = random_dates(starting_date, ending_date, rng, n_samples)
    process_date = creation_dates.copy()
    done_start_date = done_dates.copy()
    descriptions = random_descriptions(failures, regular, TOTAL_POSSIBILITY_FAILURES, rng, n_samples)
    types, todo, dones = description_parts(descriptions)

    df_dict.update(
        VorgangsID=event_ids,
        ObjektID=obj_ids,
        HObjektText=txts,
        VorgangsTypName=types,
        VorgangsBeschreibung=todo,
        ErledigungsBeschreibung=dones,
        ErstellungsDatum=creation_dates,
        VorgangsDatum=process_date,
        Arbeitsbeginn=done_start_date,
        ErledigungsDatum=done_dates,
    )
    df = pd.DataFrame.from_dict(df_dict)
    df = df.sort_values(by='ErstellungsDatum', ascending=True)
    df = df.reset_index(drop=True)
    df['VorgangsID'] = event_ids

    return df.copy()

In [13]:
df = create_dataset(
    df_skelleton=DF_SKELLETON,
    type_failure='Unerwarteter Fehler',
    type_regular='Reguläre Wartung',
    starting_date=STARTING_DATE,
    ending_date=ENDING_DATE,
    rng=RNG,
    n_samples=N_SAMPLES,
)

In [14]:
df

VorgangsID  ObjektID                    HObjektText  VorgangsTypName  \
0             1         2          Schleifmaschine-S4x87  Störungsmeldung   
1             2         2          Schleifmaschine-S4x87          Wartung   
2             3         1            Fräsmaschine-FS435X          Wartung   
3             4         3  Bohrbearbeitungszentrum-BBZ35  Störungsmeldung   
4             5         3  Bohrbearbeitungszentrum-BBZ35  Störungsmeldung   
..          ...       ...                            ...              ...   
995         996         1            Fräsmaschine-FS435X          Wartung   
996         997         2          Schleifmaschine-S4x87  Störungsmeldung   
997         998         3  Bohrbearbeitungszentrum-BBZ35          Wartung   
998         999         2          Schleifmaschine-S4x87          Wartung   
999        1000         2          Schleifmaschine-S4x87          Wartung   

                                  VorgangsBeschreibung  \
0                    Ölleckage durch undichten Ölsumpf   
1                   Überprüfung der Schwingungsdämpfer   
2                    Überprüfung der Kühlmittelsysteme   
3                       Blockierung der Förderschnecke   
4    Überhitzung durch mangelnde Kühlmittelzirkulation   
..                                                 ...   
995                          Test der Not-Aus-Schalter   
996                    Fehlfunktion der Hydraulikpumpe   
997                          Kalibrierung der Sensoren   
998                  Überprüfung der Hydraulikzylinder   
999                   Inspektion der Schutzabdeckungen   

                               ErledigungsBeschreibung ErstellungsDatum  \
0                Abdichtung und Austausch des Ölsumpfs       2022-01-01   
1      Austausch und Justierung der Schwingungsdämpfer       2022-01-03   
2      Nachfüllen und Entlüftung des Kühlmittelsystems       2022-01-05   
3    Beseitigung der Blockierung und Überprüfung de...       2022-01-06   
4    Reinigung der Leitungen und Austausch des Kühl...       2022-01-06   
..                                                 ...              ...   
995       Test und Austausch defekter Not-Aus-Schalter       2024-08-03   
996                       Austausch der Hydraulikpumpe       2024-08-05   
997                   Justierung und Test der Sensoren       2024-08-05   
998  Nachjustierung und Schmierung der Hydraulikzyl...       2024-08-05   
999   Reparatur und Austausch beschädigter Abdeckungen       2024-08-06   

    VorgangsDatum Arbeitsbeginn ErledigungsDatum  
0      2022-01-01    2022-01-01       2022-01-01  
1      2022-01-03    2022-01-03       2022-01-03  
2      2022-01-05    2022-01-05       2022-01-05  
3      2022-01-06    2022-01-07       2022-01-07  
4      2022-01-06    2022-01-09       2022-01-09  
..            ...           ...              ...  
995    2024-08-03    2024-08-03       2024-08-03  
996    2024-08-05    2024-08-06       2024-08-06  
997    2024-08-05    2024-08-07       2024-08-07  
998    2024-08-05    2024-08-05       2024-08-05  
999    2024-08-06    2024-08-07       2024-08-07  

[1000 rows x 10 columns]

In [15]:
# df.to_excel(pth_dest)

In [16]:
df.to_csv(pth_dest, sep=';', encoding='cp1252', index=False, date_format='%d.%m.%Y')

# Check processed data

In [17]:
pth_to_data = '../scripts/results/dummy_N_1000/'
pth_to_data = Path(pth_to_data)

In [29]:
files = list(pth_to_data.glob(r'*'))
files

[WindowsPath('../scripts/results/dummy_N_1000/Pipe-TargetFeature_Step-3_remove_NA.pkl'),
 WindowsPath('../scripts/results/dummy_N_1000/TIMELINE.pkl'),
 WindowsPath('../scripts/results/dummy_N_1000/Pipe-TargetFeature_Step-5_analyse_feature.pkl'),
 WindowsPath('../scripts/results/dummy_N_1000/TOKEN_ANALYSIS.pkl'),
 WindowsPath('../scripts/results/dummy_N_1000/TK-GRAPH_POSTPROCESSING.pkl'),
 WindowsPath('../scripts/results/dummy_N_1000/TokenGraph.graphml'),
 WindowsPath('../scripts/results/dummy_N_1000/TK-GRAPH_ANALYSIS.pkl'),
 WindowsPath('../scripts/results/dummy_N_1000/TokenGraph-filtered.graphml'),
 WindowsPath('../scripts/results/dummy_N_1000/TK-GRAPH_ANALYSIS_RESCALED.pkl'),
 WindowsPath('../scripts/results/dummy_N_1000/TokenGraph-directed-rescaled.graphml'),
 WindowsPath('../scripts/results/dummy_N_1000/TokenGraph-undirected-rescaled.graphml'),
 WindowsPath('../scripts/results/dummy_N_1000/token_graph.svg'),
 WindowsPath('../scripts/results/dummy_N_1000/token_graph_sub_1.svg'),
 Wi

In [22]:
from lang_main import io

A:\Arbeitsaufgaben\lang-main\.venv\Lib\site-packages\transformers\utils\generic.py:441: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(


2024-08-07 13:37:19 +0000 | lang_main:io:INFO | Loaded TOML config file successfully.


In [30]:
files[1]

WindowsPath('../scripts/results/dummy_N_1000/TIMELINE.pkl')

In [33]:
(data,) = io.load_pickle(files[1])

2024-08-07 13:51:31 +0000 | lang_main:io:INFO | Loaded file successfully.


In [34]:
data

VorgangsID  ObjektID                    HObjektText  VorgangsTypName  \
0             1         2          Schleifmaschine-S4x87  Störungsmeldung   
1             2         2          Schleifmaschine-S4x87          Wartung   
2             3         1            Fräsmaschine-FS435X          Wartung   
3             4         3  Bohrbearbeitungszentrum-BBZ35  Störungsmeldung   
4             5         3  Bohrbearbeitungszentrum-BBZ35  Störungsmeldung   
..          ...       ...                            ...              ...   
995         996         1            Fräsmaschine-FS435X          Wartung   
996         997         2          Schleifmaschine-S4x87  Störungsmeldung   
997         998         3  Bohrbearbeitungszentrum-BBZ35          Wartung   
998         999         2          Schleifmaschine-S4x87          Wartung   
999        1000         2          Schleifmaschine-S4x87          Wartung   

                                  VorgangsBeschreibung  \
0                    Ölleckage durch undichten Ölsumpf   
1                   Überprüfung der Schwingungsdämpfer   
2                    Überprüfung der Kühlmittelsysteme   
3                       Blockierung der Förderschnecke   
4    Überhitzung durch mangelnde Kühlmittelzirkulation   
..                                                 ...   
995                          Test der Not-Aus-Schalter   
996                    Fehlfunktion der Hydraulikpumpe   
997                          Kalibrierung der Sensoren   
998                  Überprüfung der Hydraulikzylinder   
999                   Inspektion der Schutzabdeckungen   

                               ErledigungsBeschreibung ErstellungsDatum  \
0                Abdichtung und Austausch des Ölsumpfs       2022-01-01   
1      Austausch und Justierung der Schwingungsdämpfer       2022-01-03   
2      Nachfüllen und Entlüftung des Kühlmittelsystems       2022-01-05   
3    Beseitigung der Blockierung und Überprüfung de...       2022-01-06   
4    Reinigung der Leitungen und Austausch des Kühl...       2022-01-06   
..                                                 ...              ...   
995       Test und Austausch defekter Not-Aus-Schalter       2024-08-03   
996                       Austausch der Hydraulikpumpe       2024-08-05   
997                   Justierung und Test der Sensoren       2024-08-05   
998  Nachjustierung und Schmierung der Hydraulikzyl...       2024-08-05   
999   Reparatur und Austausch beschädigter Abdeckungen       2024-08-06   

    VorgangsDatum Arbeitsbeginn ErledigungsDatum  
0      2022-01-01    2022-01-01       2022-01-01  
1      2022-01-03    2022-01-03       2022-01-03  
2      2022-01-05    2022-01-05       2022-01-05  
3      2022-01-06    2022-01-07       2022-01-07  
4      2022-01-06    2022-01-09       2022-01-09  
..            ...           ...              ...  
995    2024-08-03    2024-08-03       2024-08-03  
996    2024-08-05    2024-08-06       2024-08-06  
997    2024-08-05    2024-08-07       2024-08-07  
998    2024-08-05    2024-08-05       2024-08-05  
999    2024-08-06    2024-08-07       2024-08-07  

[1000 rows x 10 columns]

In [35]:
t = data.copy()

In [37]:
t['ErledigungsDatum'].dt

AttributeError: Can only use .dt accessor with datetimelike values

In [38]:
t['ErstellungsDatum'].dt

AttributeError: Can only use .dt accessor with datetimelike values

In [36]:
t['test'] = t['ErledigungsDatum'] - t['ErstellungsDatum']

TypeError: unsupported operand type(s) for -: 'str' and 'str'